In [ ]:
import ee
import folium
import json

# Authenticate and initialize Earth Engine
ee.Authenticate()
ee.Initialize(project = "ee-moethirizun97")



In [4]:
# Load the OSM Water Layer dataset
osm_water = ee.ImageCollection("projects/sat-io/open-datasets/OSM_waterLayer")

# Retrieve metadata
info = osm_water.getInfo()

# Print metadata keys
print("Metadata Keys:", info.keys())

# Pretty print the metadata
print(json.dumps(info, indent=2))


Metadata Keys: dict_keys(['type', 'bands', 'version', 'id', 'properties', 'features'])
{
  "type": "ImageCollection",
  "bands": [],
  "version": 1601448723939839,
  "id": "projects/sat-io/open-datasets/OSM_waterLayer",
  "properties": {
    "system:description": "##\u00a0OSM Water Layer: Surface Waters in OpenStreetMap\n\n\n#### Resolution: 90m\n\n#### Raster Values\n\n* 1: Ocean\n* 2: Large Lake/River\n* 3: Major River\n* 4: Canal\n* 5: Small Stream\n\n#### Citation:\nYamazaki, Dai, Daiki Ikeshima, Jeison Sosa, Paul D. Bates, George H. Allen, and Tamlin M. Pavelsky. \"MERIT Hydro: a high\u2010resolution global hydrography map based on latest topography dataset.\" Water Resources Research 55, no. 6 (2019): 5053-5073.\n\n\n#### License: Creative Commons Attribution 4.0 International (CC BY 4.0)",
    "description": "##\u00a0OSM Water Layer: Surface Waters in OpenStreetMap\u00a0 \u00a0\n[![contributor](https://img.shields.io/badge/gee--awesome--datasets-data%20commons%20contributor-gree

In [5]:
# Median aggregation of the OSM Water dataset
osm_water_median = osm_water.median()

# Visualization parameters
vis_params = {
    'min': 1,
    'max': 5,
    'palette': ["08306b", "08519c", "2171b5", "4292c6", "6baed6"]
}

# Function to add EE overlay to Folium map
def add_ee_layer(self, ee_image_object, vis_params, name):
    map_id_dict = ee.Image(ee_image_object).getMapId(vis_params)
    folium.raster_layers.TileLayer(
        tiles=map_id_dict['tile_fetcher'].url_format,
        attr='Map data &copy; <a href="https://earthengine.google.com/">Google Earth Engine</a>',
        name=name,
        overlay=True,
        control=True
    ).add_to(self)

# Add EE drawing method to folium
folium.Map.add_ee_layer = add_ee_layer

# Create a global map
global_map = folium.Map(location=[0, 0], zoom_start=2)

# Add the OSM Water layer to the map
global_map.add_ee_layer(osm_water_median, vis_params, 'OSM Water Global')

# Add a layer control panel
global_map.add_child(folium.LayerControl())

# Display the map
global_map


In [ ]:
countries = ee.FeatureCollection("FAO/GAUL/2015/level0")
australia = countries.filter(ee.Filter.eq('ADM0_NAME', 'Australia'))

# Correct region extraction for the export
australia_geometry = australia.geometry()
region = australia_geometry.bounds().getInfo()['coordinates']

# Export the dataset as a GeoTIFF
task = ee.batch.Export.image.toDrive(
    image=osm_water_australia,
    description="OSM_Water_Australia",
    region=region,  # Use the corrected region
    scale=30,  # Adjust scale as necessary
    crs="EPSG:4326",  # Optional CRS
    maxPixels=1e13
)

# Start the export task
task.start()

print("Export task started. Check your Google Drive for the file.")


Export task started. Check your Google Drive for the file.
